In [1]:
from federation.generate_scenarios import query_time_series_data, fill_null_remove_outliers, generate_scenarios
from schema.schema import Irradiation, WindSpeed, Temperature
DB_CACHE_FILE = r"../.cache/interim/time_series_schema.db"
data = query_time_series_data(DB_CACHE_FILE, alt=2510, tables=[Irradiation])["Irradiation"]
data = fill_null_remove_outliers(data, d_time="1h", z_score=10)
data_scenarios1 = generate_scenarios(data)
data = query_time_series_data(DB_CACHE_FILE, alt=2510, tables=[WindSpeed])["WindSpeed"]
data = fill_null_remove_outliers(data, d_time="1h", z_score=10)
data_scenarios2 = generate_scenarios(data)
data = query_time_series_data(DB_CACHE_FILE, alt=2510, tables=[Temperature])["Temperature"]
data = fill_null_remove_outliers(data, d_time="1h", z_score=10)
data_scenarios3 = generate_scenarios(data)

In [3]:
import polars as pl
data_df1 = data_scenarios1.filter(pl.col("scenario")=="min").select(["timestamp", "value"]).to_pandas().set_index("timestamp")["value"].asfreq("1H").fillna(0)
data_df2 = data_scenarios2.filter(pl.col("scenario")=="min").select(["timestamp", "value"]).to_pandas().set_index("timestamp")["value"].asfreq("1H").fillna(0)
data_df3 = data_scenarios3.filter(pl.col("scenario")=="min").select(["timestamp", "value"]).to_pandas().set_index("timestamp")["value"].asfreq("1H").fillna(0)

In [15]:
from federation.generate_forecast import day_ahead_forecast_arima_with_lag
predict_in_sample1 = day_ahead_forecast_arima_with_lag(data_df1, non_negative=True, lag=4)
predict_in_sample2 = day_ahead_forecast_arima_with_lag(data_df2, non_negative=True, lag=0)
predict_in_sample3 = day_ahead_forecast_arima_with_lag(data_df3, non_negative=False, lag=4)

In [16]:
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "plotly_mimetype+notebook_connected"

fig1 = go.Figure()
fig1.add_trace(go.Scatter(
    x=data_df1.index.to_list(),
    y=data_df1.to_list(),
    mode="lines",
    name="actual",
))
fig1.add_trace(go.Scatter(
    x=data_df1.index.to_list(),
    y=predict_in_sample1,
    mode="lines",
    name="DA forecast",
))
fig1.show()

fig2 = go.Figure()
fig2.add_trace(go.Scatter(
    x=data_df2.index.to_list(),
    y=data_df2.to_list(),
    mode="lines",
    name="actual",
))
fig2.add_trace(go.Scatter(
    x=data_df2.index.to_list(),
    y=predict_in_sample2,
    mode="lines",
    name="DA forecast",
))
fig2.show()

fig3 = go.Figure()
fig3.add_trace(go.Scatter(
    x=data_df3.index.to_list(),
    y=data_df3.to_list(),
    mode="lines",
    name="actual",
))
fig3.add_trace(go.Scatter(
    x=data_df3.index.to_list(),
    y=predict_in_sample3,
    mode="lines",
    name="DA forecast",
))
fig3.show()